In [1]:
import pandas as pd
import numpy as np
import altair as alt

In [2]:
df = pd.read_csv("ds_salaries.csv")

In [3]:
df.head()

work_year experience_level employment_type                 job_title  \
0       2023               SE              FT  Principal Data Scientist   
1       2023               MI              CT               ML Engineer   
2       2023               MI              CT               ML Engineer   
3       2023               SE              FT            Data Scientist   
4       2023               SE              FT            Data Scientist   

   salary salary_currency  salary_in_usd employee_residence  remote_ratio  \
0   80000             EUR          85847                 ES           100   
1   30000             USD          30000                 US           100   
2   25500             USD          25500                 US           100   
3  175000             USD         175000                 CA           100   
4  120000             USD         120000                 CA           100   

  company_location company_size  
0               ES            L  
1               US            S  
2               US            S  
3               CA            M  
4               CA            M

In [4]:
#Data Clean-up

In [5]:
#Let's see how many regions are actually represented in this dataset.
df.company_location.unique()

array(['ES', 'US', 'CA', 'DE', 'GB', 'NG', 'IN', 'HK', 'NL', 'CH', 'CF',
       'FR', 'FI', 'UA', 'IE', 'IL', 'GH', 'CO', 'SG', 'AU', 'SE', 'SI',
       'MX', 'BR', 'PT', 'RU', 'TH', 'HR', 'VN', 'EE', 'AM', 'BA', 'KE',
       'GR', 'MK', 'LV', 'RO', 'PK', 'IT', 'MA', 'PL', 'AL', 'AR', 'LT',
       'AS', 'CR', 'IR', 'BS', 'HU', 'AT', 'SK', 'CZ', 'TR', 'PR', 'DK',
       'BO', 'PH', 'BE', 'ID', 'EG', 'AE', 'LU', 'MY', 'HN', 'JP', 'DZ',
       'IQ', 'CN', 'NZ', 'CL', 'MD', 'MT'], dtype=object)

In [6]:
#What about the remote-ratio attribute?
df.remote_ratio.unique()

array([100,   0,  50], dtype=int64)

In [7]:
#Since there's so many countries represented, let's group these countries into their respective continents.
countries = df.company_location.unique()
europe_group = ['ES','DE','GB', 'NL', 'CH', 'FR', 'FI', 'UA', 'IE', 'SE', 'SI', 'PT', 'RU', 'HR', 'EE', 'AM', 'BA', 'GR',
               'MK', 'LV', 'RO','IT','PL','AL','AR','LT','HU','AT','SL','CZ','TR', 'DK','BE','LU','MD','MT', 'SK',]
print(len(europe_group))

37


In [8]:
countries = [x for x in countries if x not in europe_group]
print(countries)

['US', 'CA', 'NG', 'IN', 'HK', 'CF', 'IL', 'GH', 'CO', 'SG', 'AU', 'MX', 'BR', 'TH', 'VN', 'KE', 'PK', 'MA', 'AS', 'CR', 'IR', 'BS', 'PR', 'BO', 'PH', 'ID', 'EG', 'AE', 'MY', 'HN', 'JP', 'DZ', 'IQ', 'CN', 'NZ', 'CL']


In [9]:
north_america_group = ['US','CA','MX','PR','CR','BS','HN']
south_america_group = ['CO','BR','AR','BO','CL']
oceania_group = ['AU', 'NZ','AS',]
africa_group = ['NG', 'GH','KE','DZ','CF', 'MA', 'EG',]
asia_group = ['IN','HK','IL','SG','AE','MY','JP','CN', 'IQ', 'TH', 'VN','PK', 'IR', 'PH', 'ID','']

In [10]:
countries = [x for x in countries if x not in north_america_group and x not in south_america_group]
countries = [x for x in countries if x not in oceania_group and x not in africa_group and x not in asia_group]
print(countries)

[]


In [11]:
df['Continent of Company'] = None
df['Continent of Company'] = np.where(df['company_location'].isin(north_america_group), "North America", df['Continent of Company'])
df['Continent of Company'] = np.where(df['company_location'].isin(south_america_group), "South America", df['Continent of Company'])
df['Continent of Company'] = np.where(df['company_location'].isin(europe_group), "Europe", df['Continent of Company'])
df['Continent of Company'] = np.where(df['company_location'].isin(oceania_group), "Oceania", df['Continent of Company'])
df['Continent of Company'] = np.where(df['company_location'].isin(africa_group), "Africa", df['Continent of Company'])
df['Continent of Company'] = np.where(df['company_location'].isin(asia_group), "Asia", df['Continent of Company'])

In [12]:
df['experience_level'] = np.where(df['experience_level'] == "EN", "Entry Level", df['experience_level'])
df['experience_level'] = np.where(df['experience_level'] == "MI", "Mid Level", df['experience_level'])
df['experience_level'] = np.where(df['experience_level'] == "SE", "Senior Level", df['experience_level'])
df['experience_level'] = np.where(df['experience_level'] == "EX", "Expert Level", df['experience_level'])

In [13]:
df['company_size'] = np.where(df['company_size'] == "S", "Small", df['company_size'])
df['company_size'] = np.where(df['company_size'] == "M", "Medium", df['company_size'])
df['company_size'] = np.where(df['company_size'] == "L", "Large", df['company_size'])

In [14]:
df['remote_ratio'] = np.where(df['remote_ratio'] == 100, "Fully Remote", df['remote_ratio'])
df['remote_ratio'] = np.where(df['remote_ratio'] == '50', "Hybrid Model", df['remote_ratio'])
df['remote_ratio'] = np.where(df['remote_ratio'] == '0', "In-Person", df['remote_ratio'])
df.remote_ratio.unique()
df = df.rename(columns={'remote_ratio': "Work Type"})

In [15]:
#Visualization 1: Remote Salary vs. In-Person Salary by Region (Histogram)
histogram_plot = alt.Chart(df).mark_bar().encode(
    x=alt.X('Work Type:O', title = ""),
    y=alt.Y('mean(salary_in_usd):Q', title = "Average Salary in USD"),
    color='Work Type:N',
    tooltip = [alt.Tooltip('mean(salary_in_usd):Q', title="Average Salary (USD)")]
#     tool_tip = ['salary_in_usd']
)
alt.layer(histogram_plot).facet(
    column='Continent of Company', title = ""
    )

alt.FacetChart(...)

In [16]:
#Visualization 2: Salary by region

In [17]:
heatmap = alt.Chart(df).mark_rect().encode(
    alt.X('Continent of Company:O', title='Company Location'),
    alt.Y('mean(salary_in_usd):Q', title='Average Salary (USD)'),
    color='average(salary_in_usd):Q',
    tooltip=[alt.Tooltip('Continent of Company:O', title="Continent"),
             alt.Tooltip('average(salary_in_usd):Q', title="Average Salary (USD)")
            ]
)
heatmap.display()


alt.Chart(...)

In [18]:
#Visualization 3: Size of the company vs average salary (USD), by continent and showing experience level required


In [21]:
oceania_scatterplot = alt.Chart(df).mark_circle().encode(
    #x="Continent of Company",
    x=alt.X("average(salary_in_usd)", title = "Average Salary (USD)"),
#     y=alt.Y("work_year:N", title = "Year"),
    y=alt.Y("company_location:O", title = "Country"),
    color=alt.Color('experience_level',title = "Experience Level", sort = ["Entry Level", "Mid Level", "Senior Level", "Expert Level"], scale=alt.Scale(scheme='spectral',reverse=True)),
    size= alt.Size("company_size", title="Size of Company", sort=["Small","Medium","Large"]),
    tooltip=[alt.Tooltip('company_location:O', title="Country"),
             alt.Tooltip('average(salary_in_usd):Q', title="Average Salary (USD)"),
             alt.Tooltip('company_size', title="Company Size")
            ]
).transform_filter(
    (alt.datum["Continent of Company"] == "Oceania")
).properties(
    height=100,
    width=300,
    title = "Oceania"
)
    

asia_scatterplot = alt.Chart(df).mark_circle().encode(
    x=alt.X("average(salary_in_usd)", title = "Average Salary (USD)"),
    y=alt.Y("company_location:O", title = "Country"),
    color=alt.Color('experience_level',title = "Experience Level", sort = ["Entry Level", "Mid Level", "Senior Level", "Expert Level"], scale=alt.Scale(scheme='spectral',reverse=True)),
    size= alt.Size("company_size", title="Size of Company", sort=["Small","Medium","Large"]),
    tooltip=[alt.Tooltip('company_location:O', title="Country"),
             alt.Tooltip('average(salary_in_usd):Q', title="Average Salary (USD)"),
             alt.Tooltip('company_size', title="Company Size")
            ]
).transform_filter(
    (alt.datum["Continent of Company"] == "Asia")
).properties(
    height=200,
    width=300,
    title="Asia"
)

NA_scatterplot = alt.Chart(df).mark_circle().encode(
    x=alt.X("average(salary_in_usd)", title = "Average Salary (USD)"),
    y=alt.Y("company_location:O", title = "Country"),
    color=alt.Color('experience_level',title = "Experience Level", sort = ["Entry Level", "Mid Level", "Senior Level", "Expert Level"], scale=alt.Scale(scheme='spectral',reverse=True)),
    size= alt.Size("company_size", title="Size of Company", sort=["Small","Medium","Large"]),
    tooltip=[alt.Tooltip('company_location:O', title="Country"),
             alt.Tooltip('average(salary_in_usd):Q', title="Average Salary (USD)"),
             alt.Tooltip('company_size', title="Company Size")
            ]
).transform_filter(
    (alt.datum["Continent of Company"] == "North America")
).properties(
    height=200,
    width=300,
    title="North America"
)

SA_scatterplot = alt.Chart(df).mark_circle().encode(
    x=alt.X("average(salary_in_usd)", title = "Average Salary (USD)"),
    y=alt.Y("company_location:O", title = "Country"),
    color=alt.Color('experience_level',title = "Experience Level", sort = ["Entry Level", "Mid Level", "Senior Level", "Expert Level"], scale=alt.Scale(scheme='spectral',reverse=True)),
    size= alt.Size("company_size", title="Size of Company", sort=["Small","Medium","Large"]),
    tooltip=[alt.Tooltip('company_location:O', title="Country"),
             alt.Tooltip('average(salary_in_usd):Q', title="Average Salary (USD)"),
             alt.Tooltip('company_size', title="Company Size")
            ]
).transform_filter(
    (alt.datum["Continent of Company"] == "South America")
).properties(
    height=200,
    width=300,
    title="South America"
)

Africa_scatterplot = alt.Chart(df).mark_circle().encode(
    x=alt.X("average(salary_in_usd)", title = "Average Salary (USD)"),
    y=alt.Y("company_location:O", title = "Country"),
    color=alt.Color('experience_level',title = "Experience Level", sort = ["Entry Level", "Mid Level", "Senior Level", "Expert Level"], scale=alt.Scale(scheme='spectral',reverse=True)),
    size= alt.Size("company_size", title="Size of Company", sort=["Small","Medium","Large"]),
    tooltip=[alt.Tooltip('company_location:O', title="Country"),
             alt.Tooltip('average(salary_in_usd):Q', title="Average Salary (USD)"),
             alt.Tooltip('company_size', title="Company Size")
            ]
).transform_filter(
    (alt.datum["Continent of Company"] == "Africa")
).properties(
    height=200,
    width=300,
    title = "Africa"
)

Europe_scatterplot = alt.Chart(df).mark_circle().encode(
    x=alt.X("average(salary_in_usd)", title = "Average Salary (USD)"),
    y=alt.Y("company_location:O", title = "Country"),
    color=alt.Color('experience_level',title = "Experience Level", sort = ["Entry Level", "Mid Level", "Senior Level", "Expert Level"], scale=alt.Scale(scheme='spectral',reverse=True)),
    size= alt.Size("company_size", title="Size of Company", sort=["Small","Medium","Large"]),
    tooltip=[alt.Tooltip('company_location:O', title="Country"),
             alt.Tooltip('average(salary_in_usd):Q', title="Average Salary (USD)"),
             alt.Tooltip('company_size', title="Company Size")
            ]
).transform_filter(
    (alt.datum["Continent of Company"] == "Europe")
).properties(
    height=400,
    width=300,
    title="Europe"
)

#oceania_scatterplot | asia_scatterplot | NA_scatterplot | SA_scatterplot | Europe_scatterplot | Africa_scatterplot

alt.vconcat((Africa_scatterplot| Europe_scatterplot), (asia_scatterplot|oceania_scatterplot), (NA_scatterplot|SA_scatterplot))

alt.VConcatChart(...)

In [22]:
#Export all three visualizations to HTML:
#Visualization 1:
histogram_plot.save('Work_Type_vs_Average_USD_Salary_by_continent.html')

#Visualization 2:
heatmap.save("Average_USD_Salary_vs_Region_Heatmap.html")

#visualization 3:
scatter_plot_grid = alt.vconcat((Africa_scatterplot| Europe_scatterplot), (asia_scatterplot|oceania_scatterplot), (NA_scatterplot|SA_scatterplot))
scatter_plot_grid.save("Country_vs_Average_USD_Salary_by_continent.html")